# Deep Otello AI

The game reversi is a very good game to apply deep learning methods to.

Othello also known as reversi is a board game first published in 1883 by eiter Lewis Waterman or John W. Mollet in England (each one was denouncing the other as fraud).
It is a strickt turn based zero-sum game with a clear Markov chain and now hidden states like in card games with an unknown distribution of cards or unknown player allegiance.
There is like for the game go only one set of stones with two colors which is much easier to abstract than chess with its 6 unique pieces.
The game has a symmetrical game board wich allows to play with rotating the state around an axis to allow for a breaking of sequences or interesting ANN architectures, quadruple the data generation by simulation or interesting test cases where a symetry in turns should be observable if the AI reaches an "objective" policy.


## Content

* [The game rules](#the-game-rules) A short overview over the rules of the game.
* [Some common Otello strategies](#some-common-otello-strategies) introduces some easy approaches to a classic Otello AI and defines some behavioral expectations.
* [Initial design decisions](#initial-design-decisions) an explanation about some initial design decision and assumptions
* [Imports and dependencies](#imports-and-dependencies) explains what libraries where used


## The game rules

Othello is played on a board with 8 x 8 fields for two player.
The board geometry is equal to a chess game.
The game is played with game stones that are black on one siede and white on the other.
![Othello game board example](reversi_example.png)
The player take turns.
A player places a stone with his or her color up on the game board.
The player can only place stones when he surrounds a number of stones with the opponents color with the new stone and already placed stones of his color.
Those surrounded stones can either be horizontally, vertically and/or diagonally be placed.
All stones thus surrounded will be flipped to be of the players color.
Turns are only possible if the player is also changing the color of the opponents stones. If a player can't act he is skipped.
The game ends if both players can't act. The player with the most stones wins.
If the score is counted in detail unclaimed fields go to the player with more stones of his or her color on the board.
The game begins with four stones places in the center of the game. Each player gets two. They are placed diagonally to each other.


<img alt="Startaufstellung.png" src="Startaufstellung.png"/>

## Some common Othello strategies

As can be easily understood the placement of stones and on the bord is always a careful balance of attack and defence.
If the player occupies huge homogenous stretches on the board it can be attacked easier.
The boards corners provide safety from wich occupied territory is impossible to loos but since it is only possible to reach the corners if the enemy is forced to allow this or calculates the cost of giving a stable base to the enemy it is difficult to obtain.
There are some text on otello computer strategies which implement greedy algorithms for reversi based on a modified score to each field.
Those different values are score modifiers for a traditional greedy algorithm.
If a players stone has captured such a filed the score reached is multiplied by the modifier.
The total score is the score reached by the player subtracted with the score of the enemy.
The scores change in the course of the game and converges against one. This gives some indications of what to expect from an Othello AI.

<img alt="ComputerPossitionScore" src="computer-score.png"/>


## Initial design decisions

At the beginning of this project I made some design decisions.
The first onw was that I do not want to use a gym library because it limits the data formats accessible.
I choose to implement the hole game as entry in a stack in numpy arrays to be able to accommodate interfacing with a neural network easier and to use scipy pattern recognition tools to implement some game mechanics for a fast simulation cycle.
I chose to ignore player colors as far as I could instead a player perspective was used. Which allowed to change the perspective with a flipping of the sign. (multiplying with -1).
The array format should also allow for data multiplication or the breaking of strikt sequences by flipping the game along one the for axis, (horizontal, vertical, transpose along both diagonals).

I wanted to implement different agents as classes that act on those game stacks.

Since computation time is critical all computational have results are saved.
The analysis of those is then repeated in real time. If a recalculation of such a section is required the save file can be deleted and the code should be executed again.

In [27]:

import os.path
import warnings


%load_ext blackcellmagic

## Imports and dependencies

The following direct dependencies where used for this project:
```toml
jupyter = "^1.0.0"
matplotlib = "^3.6.3"
numpy = "^1.24.1"
pytest = "^7.2.1"
python = "3.10.*"
scipy = "^1.10.0"
tqdm = "^4.64.1"
jupyterlab = "^3.6.1"
torchvision = "^0.14.1"
torchaudio = "^0.13.1"
```
* `Jupyter` and `jupyterlab` on pycharm was used as a IDE / Ipython was used to implement this code.
* `matplotlib` was used for visualisation and statistics.
* `numpy` was used for array support and mathematical functions
* `tqdm` was used for progress bars
* `scipy` contains fast pattern recognition tools for images. It was used to make an initial estimation about where possible turns should be.
* `torch` supplied the ANN functionalities.

In [28]:
import itertools
import numpy as np
import abc
from typing import Final
from scipy.ndimage import binary_dilation
from abc import ABC
from tqdm.notebook import tqdm
from ipywidgets import interact
import matplotlib.pyplot as plt

## Constants

Some general constants needed to be defined. Such as board game size and Player and Enemy representations. Also, directional offsets and the initial placement of blocks.

In [29]:
BOARD_SIZE: Final[int] = 8  # defines the board side length as 8
PLAYER: Final[int] = 1  # defines the number symbolising the player as 1
ENEMY: Final[int] = -1  # defines the number symbolising the enemy as -1
EXAMPLE_STACK_SIZE: Final[int] = 1000  # defines the game stack size for examples
IMPOSSIBLE: Final[np.ndarray] = np.array([-1, -1], dtype=int)
IMPOSSIBLE.setflags(write=False)
SIMULATE_TURNS: Final[int] = 70
VERIFY_POLICY: Final[bool] = True

The directions array contains all the numerical offsets needed to move along one of the 8 directions in a 2 dimensional grid. This will allow an iteration over the game board.
![8-directions.png](8-directions.png "Offset in 8 directions")

In [30]:
DIRECTIONS: Final[np.ndarray] = np.array(
    [[i, j] for i in range(-1, 2) for j in range(-1, 2) if j != 0 or i != 0],
    dtype=int,
)
DIRECTIONS.setflags(write=False)
DIRECTIONS

Another constant needed is the initial start square at the center of the board.

In [31]:
START_SQUARE: Final[np.ndarray] = np.array(
    [[ENEMY, PLAYER], [PLAYER, ENEMY]], dtype=int
)
START_SQUARE.setflags(write=False)
START_SQUARE

## Creating new boards

The first function implemented and tested is a function to generate the starting environment as a stack of games.
As described above I simply placed a 2 by 2 square in the center of an empty stack of boards.

In [32]:
def get_new_games(number_of_games: int) -> np.ndarray:
    """Generates a stack of initialised game boards.

    Args:
        number_of_games: The size of the board stack.

    Returns: The generates stack of games as a stack n x 8 x 8.

    """
    empty = np.zeros([number_of_games, BOARD_SIZE, BOARD_SIZE], dtype=int)
    empty[:, 3:5, 3:5] = START_SQUARE
    return empty


get_new_games(1)[0]

In [33]:
test_number_of_games = 3
assert get_new_games(test_number_of_games).shape == (
    test_number_of_games,
    BOARD_SIZE,
    BOARD_SIZE,
)
np.testing.assert_equal(
    get_new_games(test_number_of_games).sum(axis=1),
    np.zeros(
        [
            test_number_of_games,
            8,
        ]
    ),
)
np.testing.assert_equal(
    get_new_games(test_number_of_games).sum(axis=2),
    np.zeros(
        [
            test_number_of_games,
            8,
        ]
    ),
)
assert np.all(get_new_games(test_number_of_games)[:, 3:4, 3:4] != 0)
del test_number_of_games

## Visualisation tools

In this section a visualisation help was implemented for debugging of the game and a proper display of the results.
For this visualisation ChatGPT was used as a prompted code generator that was later reviewed and refactored by hand to integrate seamlessly into the project as a whole.
White stones represent the player, black stones the enemy. A single plot can be used as a subplot when the `ax` argument is used.

In [34]:
def plot_othello_board(board: np.ndarray, ax=None) -> None:
    """Plots a single otello board.

    If a matplot axis object is given the board will be plotted into that axis. If not an axis object will be generated.
    The image generated will be shown directly.

    Args:
        board: The bord that should be plotted. Only a single games is allowed. A numpy array of the form 8x8 is expected.
        ax: If needed a matplotlib axis object can be defined that is used to place the board as a sublot into a bigger context.
    """
    assert board.shape == (8, 8)
    plot_all = False
    if ax is None:
        fig_size = 3
        plot_all = True
        fig, ax = plt.subplots(figsize=(fig_size, fig_size))

    ax.set_facecolor("#66FF00")
    for x_pos, y_pos in itertools.product(range(BOARD_SIZE), range(BOARD_SIZE)):
        if board[x_pos, y_pos] == -1:
            color = "white"
        elif board[x_pos, y_pos] == 1:
            color = "black"
        else:
            continue
        ax.scatter(y_pos, x_pos, s=300 if plot_all else 150, c=color)
    for x_pos in range(-1, 8):
        ax.axhline(x_pos + 0.5, color="black", lw=2)
        ax.axvline(x_pos + 0.5, color="black", lw=2)
    ax.set_xlim(-0.5, 7.5)
    ax.set_ylim(7.5, -0.5)
    ax.set_xticks(np.arange(8))
    ax.set_xticklabels(list("ABCDEFGH"))
    ax.set_yticks(np.arange(8))
    ax.set_yticklabels(list("12345678"))
    if plot_all:
        plt.tight_layout()
        plt.show()


plot_othello_board(get_new_games(1)[0])

In [35]:
def plot_othello_boards(boards: np.ndarray) -> None:
    """Plots multiple boards into subplots.

    The plots are shown directly.

    Args:
        boards: Plots the boards given into subplots. The maximum number of boards accepted is 70.
    """
    assert len(boards.shape) == 3
    assert boards.shape[1:] == (BOARD_SIZE, BOARD_SIZE)
    assert boards.shape[0] < 70

    plots_per_row = 4
    rows = int(np.ceil(boards.shape[0] / plots_per_row))
    fig, axs = plt.subplots(rows, plots_per_row, figsize=(12, 3 * rows))
    for game_index, ax in enumerate(axs.flatten()):
        if game_index >= boards.shape[0]:
            fig.delaxes(ax)
        else:
            plot_othello_board(boards[game_index], ax)
    plt.tight_layout()
    plt.show()

In [36]:
def drop_duplicate_boards(boards: np.ndarray) -> np.ndarray:
    """Drop boards that follow each other and are duplicates will be dropped.

    Args:
        boards: A set of boards to be reduced.

    Returns:
        A sequence of boards where boards that where equal are dropped.
    """
    return boards[~np.all(boards == np.roll(boards, axis=0, shift=1), axis=(1, 2))]

## Find possible actions to take

The frist step in the implementation of an AI like this is to get an overview over the possible actions that can be taken in a situation.
Here was the design choice taken to first find fields that are empty and have at least one neighbouring enemy stone.
This was implemented with element wise check for a stone and a binary dilation marking all fields neighboring an enemy stone.
For that the `SURROUNDING` mask was used. Both aries are then element wise combined using and.
The resulting array contains all filed where a turn could potentially be made. Those are then check in detail.
The previous element wise operations on the numpy array increase the spead for this operation dramatically.

The check for a possible turn is done in detail by following each direction step by step as long as there are enemy stones in that direction.
If the board end is reached or en empty filed before reaching a field occupied by the player that direction does not surround enemy stones.
If one direction surrounds enemy stone a turn is possible.
This detailed step is implemented as a recursion and need to go at leas one step to return True.

In [37]:
SURROUNDING: Final = np.array(
    [[[1, 1, 1], [1, 0, 1], [1, 1, 1]]]
)  # defines the binary dilation mask to check if a field is next to an enemy stones
SURROUNDING

In [38]:
def _recursive_steps(
    board: np.ndarray,
    rec_direction: np.ndarray,
    rec_position: np.ndarray,
    step_one: int = 0,
) -> int:
    """Check if a player can place a stone on the board specified in the direction specified and direction specified.

    Args:
        board: The board that should be checked for a playable action.
        rec_direction: The direction that should be checked.
        rec_position: The position that should be checked.
        step_one: Defines if the call of this function is the firs or not. Should be kept to the default value for proper functionality.

    Returns:
        True if a turn is possible for possition and direction on the board defined.
    """
    rec_position = rec_position + rec_direction
    if np.any((rec_position >= BOARD_SIZE) | (rec_position < 0)):
        return 0
    next_field = board[tuple(rec_position.tolist())]
    if next_field == 0:
        return 0
    if next_field == -1:
        return _recursive_steps(
            board, rec_direction, rec_position, step_one=step_one + 1
        )
    if next_field == 1:
        return step_one


def get_possible_turns(boards: np.ndarray, tqdm_on: bool = False) -> np.ndarray:
    """Analyses a stack of boards.

    Args:
        boards: A stack of boards to check.

    Returns:
        A stack of game boards containing boolean values showing where turns are possible for the player.
    """
    assert len(boards.shape) == 3, "The number fo input dimensions does not fit."
    assert boards.shape[1:] == (
        BOARD_SIZE,
        BOARD_SIZE,
    ), "The input dimensions do not fit."

    _poss_turns = boards == 0  # checks where fields are empty.
    _poss_turns &= binary_dilation(
        boards == -1, SURROUNDING
    )  # checks where fields are next to an enemy filed an empty
    iterate_over = itertools.product(
        range(boards.shape[0]), range(BOARD_SIZE), range(BOARD_SIZE)
    )
    if tqdm_on:
        iterate_over = tqdm(iterate_over, total=np.prod(boards.shape))
    for game, idx, idy in iterate_over:
        if _poss_turns[game, idx, idy]:
            position = idx, idy
            _poss_turns[game, idx, idy] = any(
                _recursive_steps(boards[game, :, :], direction, position) > 0
                for direction in DIRECTIONS
            )
    return _poss_turns


# some simple testing to ensure the function works after simple changes
# this testing is complete, its more of a smoke-test
test_array = get_new_games(3)
expected_result = np.zeros_like(test_array, dtype=bool)
expected_result[:, 4, 5] = expected_result[:, 2, 3] = True
expected_result[:, 5, 4] = expected_result[:, 3, 2] = True
np.testing.assert_equal(get_possible_turns(test_array), expected_result)


%timeit get_possible_turns(get_new_games(10))  # checks turn possibility evaluation time for 10 initial games
%timeit get_possible_turns(get_new_games(EXAMPLE_STACK_SIZE))  # check turn possibility evaluation time for EXAMPLE_STACK_SIZE initial games

# shows a singe game
get_possible_turns(get_new_games(3))[:1]

Besides the ability to generate an array of possible turns there needs to be a functions that check if a given turn is possible.
On is needed for the action space validation. The other is for validating a players turn.

In [ ]:
def move_possible(board: np.ndarray, move: np.ndarray) -> bool:
    """Checks if a turn is possible.

    Checks if a turn is possible. If no turn is possible to input array [-1, -1] is expected.

    Args:
        board: A board where it should be checkt if a turn is possible.
        move: The move that should be taken. Expected is the index of the filed where a stone should be placed [x, y]. If no placement is possible [-1, -1] is expected as an input.

    Returns:
        True if the move is possible
    """
    if np.all(move == -1):
        return not np.any(get_possible_turns(np.reshape(board, (1, 8, 8))))
    return any(
        _recursive_steps(board[:, :], direction, move) > 0 for direction in DIRECTIONS
    )


# Some testing for this function and the underlying recursive functions that are called.
assert move_possible(get_new_games(1)[0], np.array([2, 3])) is True
assert move_possible(get_new_games(1)[0], np.array([3, 2])) is True
assert move_possible(get_new_games(1)[0], np.array([2, 2])) is False
assert move_possible(np.zeros((8, 8)), np.array([3, 2])) is False
assert move_possible(np.ones((8, 8)) * 1, np.array([-1, -1])) is True
assert move_possible(np.ones((8, 8)) * -1, np.array([-1, -1])) is True
assert move_possible(np.ones((8, 8)) * 0, np.array([-1, -1])) is True

In [ ]:
def moves_possible(boards: np.ndarray, moves: np.ndarray) -> np.ndarray:
    """Checks if a stack of moves can be executed on a stack of boards.

    Args:
        boards: A board where the next stone should be placed.
        moves: A stack stones to be placed. Each move is formatted as an array in the form of [x, y] if no turn is possible the value [-1, -1] is expected.

    Returns:
        An array marking for each and every game and move in the stack if the move can be executed.
    """
    arr_moves_possible = np.zeros(boards.shape[0], dtype=bool)
    for game in range(boards.shape[0]):
        if np.all(
            moves[game] == -1
        ):  # can be all or any. All should be faster since most times neither value will be -1.
            arr_moves_possible[game] = not np.any(
                get_possible_turns(np.reshape(boards[game], (1, 8, 8)))
            )
        else:
            arr_moves_possible[game] = any(
                _recursive_steps(boards[game, :, :], direction, moves[game]) > 0
                for direction in DIRECTIONS
            )
    return arr_moves_possible


np.testing.assert_array_equal(
    moves_possible(np.ones((3, 8, 8)) * 1, np.array([[-1, -1]] * 3)),
    np.array([True] * 3),
)

np.testing.assert_array_equal(
    moves_possible(get_new_games(3), np.array([[2, 3], [3, 2], [3, 2]])),
    np.array([True] * 3),
)
np.testing.assert_array_equal(
    moves_possible(get_new_games(3), np.array([[2, 2], [1, 1], [0, 0]])),
    np.array([False] * 3),
)
np.testing.assert_array_equal(
    moves_possible(np.ones((3, 8, 8)) * -1, np.array([[-1, -1]] * 3)),
    np.array([True] * 3),
)
np.testing.assert_array_equal(
    moves_possible(np.zeros((3, 8, 8)), np.array([[-1, -1]] * 3)),
    np.array([True] * 3),
)

## Reword functions

For any kind of reinforcement learning is a reword function needed.
For otello this would be the final score, the information who won or changes to the score.
A combination of those three would also be possible.
It is probably not be possible to weight the current score to high in a reword function since that would be to close to a classic greedy algorithm.
But some direct influence would increase the learning speed.
In the next section are all three reword functions implemented to be combined and weight later on as needed.

In [ ]:
def final_boards_evaluation(boards: np.ndarray) -> np.ndarray:
    """Evaluates the board at the end of the game.

    All unused fields are added to the score of the player that has more stones with his color up.
    This score only applies to the end of the game.
    Normally the score is represented by the number of stones each player has.
    In this case the score was combined by building the difference.

    Args:
        boards: A stack of game bords ot the end of the game.

    Returns:
        the combined score for both player.
    """
    score1, score2 = np.sum(boards == 1, axis=(1, 2)), np.sum(boards == -1, axis=(1, 2))
    player_1_won = score1 > score2
    player_2_won = score1 < score2
    score1_final = 64 - score2[player_1_won]
    score2_final = 64 - score1[player_2_won]
    score1[player_1_won] = score1_final
    score2[player_2_won] = score2_final
    return score1 - score2


def evaluate_boards(boards: np.ndarray) -> np.ndarray:
    """Counts the stones each player has on the board.

    Args:
        boards: A stack of boards for evaluation.

    Returns:
        the combined score for both player.
    """
    return np.sum(boards, axis=(1, 2))


def evaluate_who_won(boards: np.ndarray) -> np.ndarray:
    """Checks who won or is winning a game.

    Args:
        boards: A stack of boards for evaluation.

    Returns:
        The information who won for both player. 1 meaning the player won, -1 means the opponent lost. 0 represents a patt.
    """
    return np.sign(np.sum(boards, axis=(1, 2)))


_boards = get_new_games(EXAMPLE_STACK_SIZE)
%timeit final_boards_evaluation(_boards)
%timeit evaluate_boards(_boards)
%timeit evaluate_who_won(_boards)

## Execute a chosen action

After an evaluation what turns are possible there needs to be a function that executes a turn.
This next sections does that.

In [ ]:
class InvalidTurn(ValueError):
    """
    This error is thrown if a given turn is not valid.
    """

In [ ]:
def do_moves(boards: np.ndarray, moves: np.ndarray) -> np.ndarray:
    """Executes a single move on a stack o Othello boards.

    Args:
        boards: A stack of Othello boards where the next stone should be placed.
        moves: A stack of stone placement orders for the game. Formatted as coordinates in an array [x, y] of the place where the stone should be placed. Should contain [-1,-1] if no new placement is possible.

    Returns:
        The new state of the board.
    """

    def _do_directional_move(
        board: np.ndarray, rec_move: np.ndarray, rev_direction, step_one=True
    ) -> bool:
        """Changes the color of enemy stones in one direction.

        This function works recursive. The argument step_one should always be used in its default value.

        Args:
            board: A bord on which a stone was placed.
            rec_move: The position on the board in x and y where this function is called from. Will be moved by recursive called.
            rev_direction: The position where the stone was placed. Inside this recursion it will also be the last step that was checked.
            step_one: Set to true if this is the first step in the recursion. False later on.

        Returns:
            True if a stone could be flipped.
            All changes are made on the view of the numpy array and therefore not included in the return value.
        """
        rec_position = rec_move + rev_direction
        if np.any((rec_position >= 8) | (rec_position < 0)):
            return False
        next_field = board[tuple(rec_position.tolist())]
        if next_field == 0:
            return False
        if next_field == 1:
            return not step_one
        if next_field == -1:
            if _do_directional_move(board, rec_position, rev_direction, step_one=False):
                board[tuple(rec_position.tolist())] = 1
                return True
            return False

    def _do_move(_board: np.ndarray, move: np.ndarray) -> None:
        """Executes a turn on a board.

        Args:
            _board: The game board on wich to place a stone.
            move: The coordinates of a stone that should be placed. Should be formatted as an array of the form [x, y]. The value [-1, -1] is expected if no turn is possible.

        Returns:
            All changes are made on the view of the numpy array.
        """
        if np.all(move == -1):
            if not move_possible(_board, move):
                raise InvalidTurn("An action should be taken. A turn is possible.")
            return

        # noinspection PyTypeChecker
        if _board[tuple(move.tolist())] != 0:
            raise InvalidTurn("This turn is not possible.")

        action = False
        for direction in DIRECTIONS:
            if _do_directional_move(_board, move, direction):
                action = True
        if not action:
            raise InvalidTurn("This turn is not possible.")

        # noinspection PyTypeChecker
        _board[tuple(move.tolist())] = 1

    boards = boards.copy()
    for game in range(boards.shape[0]):
        _do_move(boards[game], moves[game])
    return boards


%timeit do_moves(get_new_games(EXAMPLE_STACK_SIZE), np.array([[2, 3]] * EXAMPLE_STACK_SIZE))[0]

plot_othello_board(
    do_moves(
        get_new_games(EXAMPLE_STACK_SIZE), np.array([[2, 3]] * EXAMPLE_STACK_SIZE)
    )[0]
)

## An abstract reversi game policy

For an easy use of policies an abstract class containing the policy generation / requests an action in an inherited instance of this class.
This class filters the policy to only propose valid actions. Inherited instance do not need to care about this. This super class also manges exploration and exploitation with the epsilon value.

In [ ]:
class GamePolicy(ABC):
    """
    A game policy. Proposes where to place a stone next.
    """

    def __init__(self, epsilon: float):
        """

        Args:
            epsilon: the epsilon / greedy value. Should be between zero and one. Set the mixture of policy and exploration. One means only the policy is used. Zero means only random policies are used. All mixtures inbetween between are possible.
        """
        if 0 > epsilon > 1:
            raise ValueError("Epsilon should be between zero and one.")
        self._epsilon: float = epsilon

    @property
    def epsilon(self):
        return self._epsilon

    @property
    @abc.abstractmethod
    def policy_name(self) -> str:
        """The name of this policy"""
        raise NotImplementedError()

    @abc.abstractmethod
    def _internal_policy(self, boards: np.ndarray) -> np.ndarray:
        """The internal policy is an unfiltered policy. It should only be called from inside this function

        Args:
            boards: A board where a policy should be calculated for.

        Returns:
            The policy for this board. Should have the same size as the boards array.
        """
        raise NotImplementedError()

    def get_policy(self, boards: np.ndarray) -> np.ndarray:
        """Calculates the policy that should be followed.

        Calculates the policy that should be followed.
        This function does include the usage of epsilon to configure greediness and exploration.

        Args:
            boards: A set of boards that show the environment where the policy should be calculated for.

        Returns:
            A vector of indices. Should be formatted as an array of the form [x, y]. The value [-1, -1] is expected if no turn is possible.
        """
        assert len(boards.shape) == 3
        assert boards.shape[1:] == (BOARD_SIZE, BOARD_SIZE)

        if self.epsilon <= 0:
            policies = np.random.rand(*boards.shape)
        else:
            policies = self._internal_policy(boards)
            if self.epsilon < 1:
                policies = policies * self.epsilon + np.random.rand(*boards.shape) * (
                    1 - self.epsilon
                )

        # todo talk to team about backpropagation of score and epsilon for greedy factor

        # todo possibly change this function to only validate the purpose turn and not all turns
        possible_turns = get_possible_turns(boards)
        policies[possible_turns == False] = -1.0
        max_indices = [
            np.unravel_index(policy.argmax(), policy.shape) for policy in policies
        ]
        policy_vector = np.array(max_indices, dtype=int)
        no_turn_possible = np.all(policy_vector == 0, 1) & (policies[:, 0, 0] == -1.0)

        policy_vector[no_turn_possible, :] = IMPOSSIBLE
        return policy_vector

## A first policy

To quantify the quality of a game AI there needs to be some benchmarks.
The easiest benchmark is to play against a random player.
The easiest player to use as a benchmark is the random player.
For this and testing purpose the random policy was implemented.

In [ ]:
class RandomPolicy(GamePolicy):
    """
    A policy playing a random turn by setting epsilon to 0.
    """

    def __init__(self, epsilon: float = 0):
        _ = epsilon
        super().__init__(epsilon=0)

    @property
    def policy_name(self) -> str:
        return "random"

    def _internal_policy(self, boards: np.ndarray) -> np.ndarray:
        pass


rnd_policy = RandomPolicy(1)
assert rnd_policy.policy_name == "random"
assert rnd_policy.epsilon == 0

rnd_policy_result = rnd_policy.get_policy(get_new_games(10))
assert np.any((5 >= rnd_policy_result) & (rnd_policy_result >= 3))

In [ ]:
class GreedyPolicy(GamePolicy):
    """
    A policy playing always one of the strongest turns.
    """

    def __init__(self, epsilon: float = 1):
        _ = epsilon
        super().__init__(1)

    @property
    def policy_name(self) -> str:
        return "greedy_policy"

    def _internal_policy(self, boards: np.ndarray) -> np.ndarray:
        policies = np.random.rand(*boards.shape)
        for game, idx, idy in itertools.product(
            range(boards.shape[0]), range(BOARD_SIZE), range(BOARD_SIZE)
        ):

            if _poss_turns[game, idx, idy]:
                position = idx, idy
                policies[game, idx, idy] += np.sum(
                    _recursive_steps(boards[game, :, :], direction, position)
                    for direction in DIRECTIONS
                )
        return policies

## Putting the game simulation together
Now it's time to bring all together for a proper simulation.

### Playing a single turn

The next function needed is used to request a policy, verify that the turn is legit and place a stone and turn enemy stones if possible.

In [ ]:
def single_turn(
    current_boards: np, policy: GamePolicy
) -> tuple[np.ndarray, np.ndarray]:
    """Execute a single turn on a board.

    Places a new stone on the board. Turns captured enemy stones.

    Args:
        current_boards: The current board before the game.
        policy: The game policy to be used.

    Returns:
        The new game board and the policy vector containing the index of the action used.
    """
    policy_results = policy.get_policy(current_boards)

    # if the constant VERIFY_POLICY is set to true the policy is verified. Should be good though.
    # todo deactivate the policy verification after some testing.
    if VERIFY_POLICY:
        assert np.all(moves_possible(current_boards, policy_results)), (
            current_boards[(moves_possible(current_boards, policy_results) == False)],
            policy_results[(moves_possible(current_boards, policy_results) == False)],
            np.where(moves_possible(current_boards, policy_results) == False),
        )
    return do_moves(current_boards, policy_results), policy_results


%timeit single_turn(get_new_games(EXAMPLE_STACK_SIZE), RandomPolicy(1))
VERIFY_POLICY = False  # type: ignore
%timeit single_turn(get_new_games(EXAMPLE_STACK_SIZE), RandomPolicy(1))
VERIFY_POLICY = True  # type: ignore
plot_othello_boards(
    single_turn(get_new_games(EXAMPLE_STACK_SIZE), RandomPolicy(1))[0][:8]
)

### Simulate a stack of games
This function will simulate a stack of games and return an array of policies and histories.

In [ ]:
def simulate_game(
    nr_of_games: int,
    policies: tuple[GamePolicy, GamePolicy],
    tqdm_on: bool = False,
) -> tuple[np.ndarray, np.ndarray]:
    """Simulates a stack of games.

    Args:
        nr_of_games: The number of games that should be simulated.
        policies: The policies that should be used to simulate the game.
        tqdm_on: Switches tqdm on.

    Returns:
        A stack of board histories and actions.
    """
    board_history_stack = np.zeros((SIMULATE_TURNS, nr_of_games, 8, 8), dtype=np.int8)
    action_history_stack = np.zeros((SIMULATE_TURNS, nr_of_games, 2), dtype=np.int8)
    current_boards = get_new_games(nr_of_games)
    for turn_index in tqdm(range(SIMULATE_TURNS)) if tqdm_on else range(SIMULATE_TURNS):
        policy_index = turn_index % 2
        policy = policies[policy_index]
        board_history_stack[turn_index, :, :, :] = current_boards
        if policy_index == 0:
            current_boards = current_boards * -1
        current_boards, action_taken = single_turn(current_boards, policy)
        action_history_stack[turn_index, :] = action_taken

        if policy_index == 0:
            current_boards = current_boards * -1

    return board_history_stack, action_history_stack


simulation_results = simulate_game(1, (RandomPolicy(1), RandomPolicy(1)))
plot_othello_boards(
    drop_duplicate_boards(np.reshape(simulation_results[0], (-1, 8, 8)))
)

In [ ]:
%timeit simulate_game(100, (RandomPolicy(1), RandomPolicy(1)))

## Statistical examination of the natural action space and result
As for many project some evaluation of the project is in order.

1. What is the expected distribution of scores
2. What is the expected distribution of possible actions
    a. over time
    b. ober space

The easiest and most robust way to analyse this is when analyzing randomly played games.

In [ ]:
if not os.path.exists("rnd_history.npy") and not os.path.exists("rnd_action.npy"):
    rnds = RandomPolicy(1), RandomPolicy(1)
    simulation_results = simulate_game(10_000, rnds, tqdm_on=True)
    _board_history, _action_history = simulation_results
    np.save("rnd_history.npy", np.astpye.astype(np.int8))
    np.save("rnd_action.npy", _action_history.astype(np.int8))
else:
    _board_history = np.load("rnd_history.npy")
    _action_history = np.load("rnd_action.npy")
print(_board_history.shape)
print(_action_history.shape)

In [ ]:
print(_board_history.shape)
print(_action_history.shape)

In [ ]:
if not os.path.exists("turn_possible.npy"):
    __board_history = _board_history.copy()
    __board_history[1::2] = __board_history[1::2] * -1

    _poss_turns = get_possible_turns(
        __board_history.reshape((-1, 8, 8)), tqdm_on=True
    ).reshape((70, -1, 8, 8))
    np.save(_poss_turns, "turn_possible.npy")
    del __board_history
_poss_turns = np.load("turn_possible.npy")
poss_turn = np.sum(_poss_turns, axis=(2, 3))
poss_turn.shape

In [ ]:
mean_possibilities = np.mean(poss_turn, axis=1)
plt.title(
    f"Mean turn possible per turn {np.prod(np.extract(mean_possibilities, mean_possibilities))}"
)
plt.plot(mean_possibilities)
plt.show()
del mean_possibilities

In [ ]:
@interact(turn=(0, 69))
def poss_turn_count(turn):
    plt.hist(poss_turn[turn])

In [ ]:
def calculate_direct_score(board_history: np.ndarray) -> np.ndarray:
    boards_evaluated = np.reshape(
        evaluate_boards(np.reshape(board_history, (-1, 8, 8))), (SIMULATE_TURNS, -1)
    )
    direct_score = boards_evaluated - np.roll(boards_evaluated, shift=-1, axis=0)
    direct_score[-1] = 0
    return direct_score / 64


assert len(calculate_direct_score(_board_history).shape) == 2
assert calculate_direct_score(_board_history).shape[0] == SIMULATE_TURNS
print(calculate_direct_score(_board_history).shape)
calculate_direct_score(_board_history)

In [ ]:
@interact(turn=(0, 69))
def hist_direct_score(turn):
    score_history = calculate_direct_score(_board_history) * 64
    score_history[1::2] = score_history[1::2] * -1
    # print(score_history[turn])
    plt.title(f"Histogram of turn {turn} by {'white' if turn % 2 == 0 else 'black'}")
    plt.hist(score_history[turn], density=True)
    plt.show()

In [ ]:
def calculate_final_evaluation_for_history(board_history: np.ndarray) -> np.ndarray:
    final_evaluation = final_boards_evaluation(board_history[-1])
    return final_evaluation / 64


assert len(calculate_final_evaluation_for_history(_board_history).shape) == 1
print(calculate_final_evaluation_for_history(_board_history).shape)
_final_eval = calculate_final_evaluation_for_history(_board_history)
plt.title("Histogram over the score distribtuion")
plt.hist((_final_eval * 64), density=True)
plt.show()

In [ ]:
def calculate_who_won(board_history: np.ndarray) -> np.ndarray:
    who_won = evaluate_who_won(board_history[-1])
    return who_won


plt.title("Histogram over the win distribtuion")
plt.hist(calculate_who_won(_board_history), density=True, bins=3)
plt.show()

In [ ]:
def history_changed(board_history: np.ndarray) -> np.ndarray:
    return ~np.all(
        np.roll(board_history, shift=1, axis=0) == board_history, axis=(2, 3)
    )


plt.title("Share of turns skipped")
plt.plot(1 - np.mean(history_changed(_board_history), axis=1))
# plt.yscale('log',base=10)
plt.show()

In [ ]:
def get_gamma_table(board_history, gamma_value: float):
    unchanged = history_changed(board_history)
    gamma_values = np.ones_like(unchanged, dtype=float)
    gamma_values[unchanged] = gamma_value
    return gamma_values


get_gamma_table(_board_history, 0.8).shape

In [ ]:
def calculate_q_reword(
    board_history: np.ndarray,
    who_won_fraction: float = 0.2,
    final_score_fraction=0.2,
    gamma=0.8,
) -> np.ndarray:
    assert who_won_fraction + final_score_fraction <= 1
    assert final_score_fraction >= 0
    assert who_won_fraction >= 0

    gama_table = get_gamma_table(board_history, gamma)
    combined_score = np.zeros_like(gama_table)
    combined_score += calculate_direct_score(board_history) * (
        1 - who_won_fraction + final_score_fraction
    )
    combined_score[-1] += calulate_final_score(board_history) * final_score_fraction
    combined_score[-1] += calculate_who_won(board_history) * who_won_fraction
    for turn in range(SIMULATE_TURNS - 1, -1, -1):
        values = gama_table[turn] * combined_score[turn]
        combined_score[turn - 1] += values

    return combined_score


np.max(calculate_q_reword(_board_history, gamma=0.8), axis=1)

In [ ]:
rewords
evaluate_boards(boards).shape

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

In [ ]:
BATCH_SIZE = 1000


class DQLNet(nn.Module):
    def __init__(self):
        super().__init__()
        self.fc1 = nn.Linear(BATCH_SIZE, 64)
        self.fc2 = nn.Linear(BATCH_SIZE, 64)

    def forward(self, x):
        if isinstance(x, np.ndarray):
            x = torch.from_numpy(x).float()
        x = torch.flatten(x, 1)
        print(x)
        x = self.fc1(x)
        print(x)
        x = F.relu(x)
        print(x)
        # x = self.dropout1(x)
        x = self.fc2(x)
        x = F.relu(x)
        # x = self.dropout2(x)
        x = torch.reshape(x, (BATCH_SIZE, 8, 8))
        return x

In [ ]:
DQLNet().fc1

In [ ]:
ones = np.ones((1000, 8, 8), dtype=float)

In [ ]:
DQLNet().forward(ones)

In [ ]:
t = torch.tensor([[[1, 2], [3, 4]], [[5, 6], [7, 8]]])
torch.flatten(t)
torch.tensor([1, 2, 3, 4, 5, 6, 7, 8])
torch.flatten(t, start_dim=1)
torch.tensor([[1, 2, 3, 4], [5, 6, 7, 8]])

In [ ]:
class DQLearningWinner(GamePolicy):

    # network =

    @property
    def policy_name(self):
        return "DQL-Winner"

    def _internal_policy(boards) -> np.ndarray:
        pass

In [ ]:
DQLearningWinner(0.9)

In [ ]:
def calculate_simple_rewords()

# Sources

* Game rules and example board images [https://en.wikipedia.org/wiki/Reversi](https://en.wikipedia.org/wiki/Reversi)
* Game rules and example game images [https://de.wikipedia.org/wiki/Othello_(Spiel)](https://de.wikipedia.org/wiki/Othello_(Spiel))
* Game strategy examples [https://de.wikipedia.org/wiki/Computer-Othello](https://de.wikipedia.org/wiki/Computer-Othello)
* Image for 8 directions [https://www.researchgate.net/journal/EURASIP-Journal-on-Image-and-Video-Processing-1687-5281](https://www.researchgate.net/journal/EURASIP-Journal-on-Image-and-Video-Processing-1687-5281)